In [89]:
from datetime import timedelta
import json
import pprint
from copy import deepcopy

import cufflinks
cufflinks.go_offline()
import numpy as np
from numpy.polynomial import Polynomial
import pandas as pd
from tqdm.notebook import tqdm

from notepad import WaterStorage, Heatpump
from pyrecoy.colors import *
from pyrecoy.converters import *
from pyrecoy.financial import calculate_eb_ode, get_tax_tables, get_tax_rate, get_grid_tariffs_electricity
from pyrecoy.framework import TimeFramework
from pyrecoy.casestudy import CaseStudy
from pyrecoy.plotting import ebitda_bar_chart, npv_bar_chart
from pyrecoy.reports import CaseReport, ComparisonReport, BusinessCaseReport, SingleFigureComparison
from pyrecoy.sensitivity import SensitivityAnalysis
from pyrecoy.prices import get_tennet_data, get_afrr_capacity_fees_nl
from pyrecoy.forecasts import Mipf

%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [90]:
class Config():
    start = '2019-01-01'
    end = '2019-12-31'
    
    hp_vdg_e_power = 23.3 # MW before
    hp_ndg_e_power = 7.7 # MW after
    hp_min_load = 0.3
    hp_lifetime = 25
    hp_capex = 200_000 # EUR/MWth
    hp_opex = 0.01 # in % of CAPEX
    hp_devex = 0.005 # in % of CAPEX
    
    gb_power = 35 # MW
    gb_efficiency = 0.9
    
    tax_bracket_g = 4 
    tax_bracket_e = 4
    
    include_transport_costs = False
    grid_operator = 'Liander'
    connection_type = 'TS/MS'
    
    discount_rate = 0.1
    project_duration = 12

    forecast = 'ForeNeg'
    gas_price_multiplier = 1
    e_price_multiplier = 1
    e_price_volatility_multiplier = 1
    co2_price_multiplier = 1
    tsource_delta = 0
    tsink_delta = 0
    energy_tax_multiplier = 1
    
    # Review the SDE implementation
    sde_base_amount = 81
    longterm_gas_price = 24.00
    longterm_co2_price = 37.90
    sde_switch_price_correction = 40
    
    day_ahead_buying_perc = 0.3
    
    afrr_capacity_fee = 25_000

c = Config()

In [91]:
class Store():
    pass

In [104]:
def load_demand_data(c, s):
    demand = pd.read_csv('data/smurfit_demand_preprocessed.csv', delimiter=';', decimal=',')
    dt_index = pd.date_range(
        start=s.time_fw.start,
        end=s.time_fw.start + timedelta(days=365), freq='1T',
        closed='left',
        tz='Europe/Amsterdam')
    demand.index = dt_index
    demand['Total demand'] = demand['MW (VDG)'] + demand['MW (NDG)']
    demand = demand[c.start:c.end]
    return demand


In [94]:
def setup_model(c):
    s = Store()
    
    s.time_fw = TimeFramework(start=c.start, end=c.end)
    mipf = Mipf(
        start=s.time_fw.start, 
        end=s.time_fw.end, 
        tidy=True, 
        include_nextQ=True, 
        folder_path=r"C:\Users\Shahla Huseynova\Recoy\Recoy - Documents\03 - Libraries\12 - Data Management\Forecast Data"
    ).data

    s.hpcase = CaseStudy(time_fw=s.time_fw, freq='1T', name='Heatpump only', data=mipf)
    s.hp_storage_case = CaseStudy(time_fw=s.time_fw, freq='1T', name='Heatpump + Storage', data=mipf)
    
    s.cases = list(CaseStudy.instances.values())
    s.optcases = [s.hpcase, s.hp_storage_case]
    # s.sde_cases = [s.hpcase_sde, s.optcase1, s.afrr_case]
    
    s.demand = load_demand_data(c, s)
    return s

s = setup_model(c)
s.optcases

c:\users\shahla huseynova\python\29 - pyrecoy modelling framework\pyrecoy\pyrecoy\framework.py:35: FutureWarning:

Argument `closed` is deprecated in favor of `inclusive`.

c:\users\shahla huseynova\python\29 - pyrecoy modelling framework\pyrecoy\pyrecoy\framework.py:35: FutureWarning:

Argument `closed` is deprecated in favor of `inclusive`.

C:\Users\SHAHLA~1\AppData\Local\Temp/ipykernel_27972/4233922362.py:3: FutureWarning:

Argument `closed` is deprecated in favor of `inclusive`.



In [95]:
demand = load_demand_data(c, s)
demand
# how this dataframe is created in the class??

C:\Users\SHAHLA~1\AppData\Local\Temp/ipykernel_27972/4233922362.py:3: FutureWarning:

Argument `closed` is deprecated in favor of `inclusive`.



Tsource (VDG)  Tsink (VDG)  MW (VDG)  \
2019-01-01 00:00:00+01:00         64.990      143.360      0.00   
2019-01-01 00:01:00+01:00         64.985      143.089      0.00   
2019-01-01 00:02:00+01:00         64.980      142.818      0.00   
2019-01-01 00:03:00+01:00         64.975      142.547      0.00   
2019-01-01 00:04:00+01:00         64.970      142.276      0.00   
...                                  ...          ...       ...   
2019-12-31 23:55:00+01:00         65.050      129.970     17.04   
2019-12-31 23:56:00+01:00         65.050      129.970     17.04   
2019-12-31 23:57:00+01:00         65.050      129.970     17.04   
2019-12-31 23:58:00+01:00         65.050      129.970     17.04   
2019-12-31 23:59:00+01:00         65.050      129.970     17.04   

                           Tsource (NDG)  Tsink (NDG)  MW (NDG)  Total demand  
2019-01-01 00:00:00+01:00         20.510      147.620      0.00          0.00  
2019-01-01 00:01:00+01:00         20.387      147.642      0.00          0.00  
2019-01-01 00:02:00+01:00         20.264      147.664      0.00          0.00  
2019-01-01 00:03:00+01:00         20.141      147.686      0.00          0.00  
2019-01-01 00:04:00+01:00         20.018      147.708      0.00          0.00  
...                                  ...          ...       ...           ...  
2019-12-31 23:55:00+01:00         67.070      129.350      5.69         22.73  
2019-12-31 23:56:00+01:00         67.070      129.350      5.69         22.73  
2019-12-31 23:57:00+01:00         67.070      129.350      5.69         22.73  
2019-12-31 23:58:00+01:00         67.070      129.350      5.69         22.73  
2019-12-31 23:59:00+01:00         67.070      129.350      5.69         22.73  

[525600 rows x 7 columns]

In [114]:
def add_afrr_prices(c, case):
    try:
        aFRR_signal = pd.read_csv(f'data/aFRR_{c.start}.csv', delimiter=';', decimal=',', index_col='datetime')
        aFRR_signal.index = case.data.index
    except:
        data = get_tennet_data('balansdelta2017', pd.to_datetime(c.start), pd.to_datetime(c.end))
        data.index = data[["datum", "tijd"]].apply(lambda x: " ".join(x), axis=1)
        data.index = pd.to_datetime(data.index, format="%d-%m-%Y %H:%M").tz_localize(
            "Europe/Amsterdam", ambiguous=True
        )
        data = data[~data.index.duplicated(keep="first")]
        date_ix = pd.date_range(
            data.index[0], data.index[-1], freq="1T", tz="Europe/Amsterdam"
        )
        data = data.reindex(date_ix)
        aFRR_signal = data[['Hoogste_prijs_opregelen', 'Mid_prijs_opregelen', 'Laagste_prijs_afregelen']]
        aFRR_signal.to_csv(f'data/aFRR_{c.start}.csv', sep=';', decimal=',', index_label='datetime')

    try:
        aFRR_prices = pd.read_csv(f'data/aFRR_prices_{c.start}.csv', delimiter=';', decimal=',', index_col='datetime')
        aFRR_prices.index = case.data.index
    except:
        data = get_aFRR_prices_nl(pd.to_datetime(c.start), pd.to_datetime(c.end))
        data.index = pd.date_range(
            start=c.start,
            end=pd.to_datetime(c.end) + timedelta(days=1),
            tz='Europe/Amsterdam', 
            freq='15T', 
            closed='left'
        )
        aFRR_prices = data.reindex(case.data.index, method='ffill')
        aFRR_prices.to_csv(f'data/aFRR_prices_{c.start}.csv', sep=';', decimal=',', index_label='datetime')
        
    case.data = pd.concat([case.data, aFRR_signal, aFRR_prices], axis=1)
    return case

In [97]:
def increase_volatility_by_factor(col, factor):
    mean = col.mean()
    diff_to_mean = col - mean
    new_diff = diff_to_mean * factor
    return mean + new_diff

def multiply_by_factor(col, factor):
    mean = col.mean()
    diff_to_mean = col - mean
    
    cond = diff_to_mean > 0
    diff_to_mean[cond] *= factor
    diff_to_mean[~cond] /= factor
    return mean + diff_to_mean

In [98]:
def load_data(c, s):
    # s.afrr_case = add_afrr_prices(c, s.afrr_case)
    
    for case in s.cases:
        case.add_gasprices()
        case.add_co2prices(perMWh=True)
        
        case.data['Gas prices (€/MWh)'] *= c.gas_price_multiplier
        case.data['CO2 prices (€/MWh)'] *= c.co2_price_multiplier
        case.data['CO2 prices (€/ton)'] *= c.co2_price_multiplier
        
    for case in s.optcases:
        case.data['NEG'] = multiply_by_factor(case.data['NEG'], c.e_price_multiplier)
        case.data['ForeNeg'] = multiply_by_factor(case.data['ForeNeg'], c.e_price_multiplier)
        case.data['DAM'] = multiply_by_factor(case.data['DAM'], c.e_price_multiplier)
        
        case.data['NEG'] = increase_volatility_by_factor(case.data['NEG'], c.e_price_volatility_multiplier)
        case.data['ForeNeg'] = increase_volatility_by_factor(case.data['ForeNeg'], c.e_price_volatility_multiplier)
        
    s.demand[['Tsource (VDG)', 'Tsource (NDG)']] += c.tsource_delta
    s.demand[['Tsink (VDG)', 'Tsink (NDG)']] += c.tsink_delta
    for case in s.cases:
        case.data = pd.concat([case.data, s.demand], axis=1)        

    s.eb_ode_g = get_tax_rate('gas', 2020, 4)['EB+ODE'] * c.energy_tax_multiplier
    s.eb_ode_e = get_tax_rate('electricity', 2020, 4)['EB+ODE'] * c.energy_tax_multiplier
    s.grid_fees = get_grid_tariffs_electricity(c.grid_operator, 2020, c.connection_type)
    s.grid_fee_per_MWh = s.grid_fees['kWh tarief'] * 1000
    return s

s = load_data(c, s)

In [106]:
def cop_value(Tsink, Tsource):
    Tsink += 273
    Tsource += 273
    
    return Tsink / (Tsink - Tsource)

In [107]:
cop_value(140, 25)

3.591304347826087

In [108]:
heatpump = Heatpump(
    name='Heatpump',
    max_th_power=1,
    min_th_power=0,
    cop_curve=cop_value
)

In [118]:
def create_and_assign_assets(c, s):
    heatpump_vdg = Heatpump(
        name='Heatpump VDG',
        max_th_power=c.hp_vdg_e_power,
        min_th_power=c.hp_vdg_e_power * c.hp_min_load,
        cop_curve=cop_value
    )

    capex_vdg = c.hp_capex*(heatpump_vdg.max_th_power) 
    heatpump_vdg.set_financials(capex=capex_vdg, opex=c.hp_opex*capex_vdg, devex=c.hp_devex*capex_vdg, lifetime=25)

    vessel = WaterStorage(
        name='MyStorage',
        max_power=10,
        min_power=-10,
        roundtrip_eff=0.90,
        specific_heat_capacity =1.16*1e-3,
        volume = 1000,
        lifetime = 25,
        min_temperature = 55 + 273,
        max_temperature = 95 + 273
    )
    capex_per_MW = 3_000
    capex_per_MWh = 10_000

    vessel.set_financials(
        capex_per_MW,
        capex_per_MWh,
        2_000,
        0,
        lifetime=30
    )
    
#     s.hp_storage_case.add_asset(vessel)
    s.baseline.add_asset(gasboiler)
    s.hpcase.add_asset(heatpump_vdg)
    s.hpcase.add_asset(heatpump_ndg)
    s.hpcase_sde.add_asset(heatpump_vdg)
    s.hpcase_sde.add_asset(heatpump_ndg)
    s.optcase1.add_asset(heatpump_vdg)
    s.optcase1.add_asset(heatpump_ndg)
    s.optcase1.add_asset(gasboiler)
    s.afrr_case.add_asset(heatpump_vdg)
    s.afrr_case.add_asset(heatpump_ndg)
    s.afrr_case.add_asset(gasboiler)
    return s

s = create_and_assign_assets(c, s)

TypeError: _set_cop_curve() takes 1 positional argument but 2 were given

In [ ]:
def vessel_charge(self, temperature):
    if case.data is NEG and load_perc =! 1
    return Tsink
    
    

In [ ]:
def vessel_discharge(self):
    if case.data is DAM and Tsource<Tsource (VDG).mean()
    return max_temperature
    # if case.data is DAM and load_perc
    

In [110]:
def cop_value_new (Tsink, Tsource_new):
    Tsink += 273
    Tsource_new = (vessel.max_temperature + Tsource).mean()
    Tsource_new +=273
    return Tsink / (Tsink - Tsource_new)

In [ ]:
Tsink =  140 + 273
Tsource = 60 + 273
HP_power = 31 